In [8]:
import pandas as pd
import datetime
import numpy as np

import CoreTraidMath 


In [9]:
df_candle = pd.read_csv(r"../data/EURUSD_price_candlestick.csv")
df_candle.rename(columns={'timestamp': 'date'}, inplace=True)
df_candle

date     open    close     high      low
0      2020-09-01 03:00:00+03:00  1.19370  1.19388  1.19391  1.19368
1      2020-09-01 03:00:05+03:00  1.19387  1.19388  1.19391  1.19383
2      2020-09-01 03:00:10+03:00  1.19387  1.19384  1.19389  1.19382
3      2020-09-01 03:00:15+03:00  1.19384  1.19384  1.19386  1.19382
4      2020-09-01 03:00:20+03:00  1.19387  1.19390  1.19391  1.19383
...                          ...      ...      ...      ...      ...
99995  2020-09-06 21:52:55+03:00  1.18382  1.18382  1.18393  1.18371
99996  2020-09-06 21:53:00+03:00  1.18382  1.18382  1.18393  1.18371
99997  2020-09-06 21:53:05+03:00  1.18382  1.18382  1.18393  1.18371
99998  2020-09-06 21:53:10+03:00  1.18382  1.18382  1.18393  1.18371
99999  2020-09-06 21:53:15+03:00  1.18382  1.18382  1.18393  1.18371

[100000 rows x 5 columns]

In [10]:
class coreIndicator():
    
    def __init__(self,options: dict, dataType: str = None, predictType: str = None, name: str = None):
        self.options = options
        self.dataType = dataType #ochl
        self.predictType = predictType #trend
        
    
    def getAns(self, data: pd.DataFrame() ):
        return "ERROR"

In [11]:
class ind_BB(coreIndicator):
    """
    options
        MeanType -> SMA
        window -> int
        valueType -> str: low, high, open, close
        kDev -> float
    
    """
    
    def __init__(self,options: dict,name = None):
        super().__init__(
            options = options,
            dataType = 'ochl',
            predictType = 'trend',
            name = name
        )
    
    def getAns(self, data: pd.DataFrame()):
        data=data.reset_index(drop=True)
        ans={}
        opMA={'dataType':'ohcl',
            'action':'findMean',
            'actionOptions':{
                'MeanType':self.options['MeanType'],
                'valueType':self.options['valueType'],
                'window':self.options['window']
            }
        }
        ans['BB']=CoreTraidMath.CoreMath(data,opMA).ans
        opSTD={'dataType':'ohcl',
            'action':'findSTD',
            'actionOptions':{'valueType':self.options['valueType'],'window':self.options['window']}
        }
        ans['STD']=CoreTraidMath.CoreMath(data,opSTD).ans
        ans['pSTD']=ans['BB']+ans['STD']*self.options['kDev']
        ans['mSTD']=ans['BB']-ans['STD']*self.options['kDev']
        ans['x']=np.array(data['date'][self.options['window']-1:].to_list())
        self.ans= ans
        return ans

In [12]:
class indicatorsAgrigator:
    
    def __init__ (self,indDict={}):
        self.indDict = indDict
        self.indInst = {}
        self.ans={}
        self.createIndicatorsInstance()
    
    def createIndicatorsInstance(self):
        for i in self.indDict.keys():
            self.indInst[i]=self.indDict[i]['className'](self.indDict[i]['params'])
            
    def getAns(self,dataDict={}):
        ans={}
        for i in dataDict.keys():
            ans[i] = self.indInst[i].getAns(dataDict[i])
        return ans

In [13]:
indicators = {
    'ind_BB':{
        'className':ind_BB,
        'params':{'MeanType':'SMA','window':15,'valueType':'close','kDev':2.5}
    }
}
dataDic={
    'ind_BB':df_candle[:1000]
}

In [14]:
ia= indicatorsAgrigator(indicators)

In [15]:
ia.__dict__

{'indDict': {'ind_BB': {'className': __main__.ind_BB,
   'params': {'MeanType': 'SMA',
    'window': 15,
    'valueType': 'close',
    'kDev': 2.5}}},
 'indInst': {'ind_BB': <__main__.ind_BB at 0x7f04f55a21d0>},
 'ans': {}}

In [16]:
ia.indInst['ind_BB'].__dict__

{'options': {'MeanType': 'SMA',
  'window': 15,
  'valueType': 'close',
  'kDev': 2.5},
 'dataType': 'ochl',
 'predictType': 'trend'}

In [17]:
ia.getAns(dataDict=dataDic)

{'ind_BB': {'BB': array([1.19389133, 1.19388733, 1.193884  , 1.193884  , 1.193884  ,
         1.19388   , 1.19387733, 1.19387467, 1.193872  , 1.19387133,
         1.19387933, 1.19389   , 1.193904  , 1.193914  , 1.193922  ,
         1.19393667, 1.19395933, 1.193982  , 1.19401067, 1.19403533,
         1.194058  , 1.19408267, 1.194108  , 1.19412933, 1.19414467,
         1.19415133, 1.19415333, 1.194156  , 1.194158  , 1.19415467,
         1.19414933, 1.194144  , 1.19413933, 1.19413533, 1.19413667,
         1.19414   , 1.19414333, 1.19414733, 1.19415533, 1.19416733,
         1.194182  , 1.19419533, 1.19420667, 1.19422067, 1.19424067,
         1.19425933, 1.19427733, 1.194292  , 1.19429933, 1.19430533,
         1.19431867, 1.19432867, 1.19433533, 1.194344  , 1.19435333,
         1.194358  , 1.194364  , 1.19437067, 1.19437933, 1.194382  ,
         1.19438533, 1.19438867, 1.194392  , 1.194396  , 1.1944    ,
         1.19439667, 1.194394  , 1.19438867, 1.19438267, 1.19438   ,
         1.1943833

In [18]:
op = {'MeanType':'SMA','window':5,'valueType':'low','kDev':2}

In [19]:
t =  ind_BB(op)

In [20]:
t.getAns(df_candle[:100])

{'BB': array([1.193796, 1.193836, 1.193842, 1.193852, 1.193862, 1.193866,
        1.193858, 1.19386 , 1.19386 , 1.19386 , 1.193872, 1.193864,
        1.193852, 1.193838, 1.193828, 1.193812, 1.193816, 1.193818,
        1.193818, 1.19382 , 1.193822, 1.193854, 1.193896, 1.19394 ,
        1.193974, 1.194018, 1.194046, 1.19407 , 1.194102, 1.194136,
        1.194154, 1.19417 , 1.194182, 1.194174, 1.194156, 1.19414 ,
        1.194114, 1.194088, 1.194072, 1.19406 , 1.194046, 1.194042,
        1.194038, 1.194042, 1.194076, 1.194116, 1.194154, 1.194188,
        1.194222, 1.194236, 1.194248, 1.19424 , 1.194246, 1.194248,
        1.194252, 1.194268, 1.19429 , 1.194296, 1.194302, 1.194304,
        1.194298, 1.194314, 1.194326, 1.194336, 1.194356, 1.194364,
        1.194356, 1.194358, 1.194368, 1.19437 , 1.194374, 1.194378,
        1.194376, 1.194368, 1.194356, 1.19435 , 1.194344, 1.19433 ,
        1.194302, 1.194302, 1.194308, 1.194318, 1.194334, 1.194366,
        1.194366, 1.194362, 1.194352, 1.19

In [21]:
t.__dict__

{'options': {'MeanType': 'SMA', 'window': 5, 'valueType': 'low', 'kDev': 2},
 'dataType': 'ochl',
 'predictType': 'trend',
 'ans': {'BB': array([1.193796, 1.193836, 1.193842, 1.193852, 1.193862, 1.193866,
         1.193858, 1.19386 , 1.19386 , 1.19386 , 1.193872, 1.193864,
         1.193852, 1.193838, 1.193828, 1.193812, 1.193816, 1.193818,
         1.193818, 1.19382 , 1.193822, 1.193854, 1.193896, 1.19394 ,
         1.193974, 1.194018, 1.194046, 1.19407 , 1.194102, 1.194136,
         1.194154, 1.19417 , 1.194182, 1.194174, 1.194156, 1.19414 ,
         1.194114, 1.194088, 1.194072, 1.19406 , 1.194046, 1.194042,
         1.194038, 1.194042, 1.194076, 1.194116, 1.194154, 1.194188,
         1.194222, 1.194236, 1.194248, 1.19424 , 1.194246, 1.194248,
         1.194252, 1.194268, 1.19429 , 1.194296, 1.194302, 1.194304,
         1.194298, 1.194314, 1.194326, 1.194336, 1.194356, 1.194364,
         1.194356, 1.194358, 1.194368, 1.19437 , 1.194374, 1.194378,
         1.194376, 1.194368, 1.19435